# Скрипт для поиска лишних и недостающих файлов на сетевом диске

Этот скрипт проверяет, какие файлы на сетевом диске не используются в лекциях и какие файлы, наоборот, должны быть в лекциях, но на сетевом диске они исчезли. Он позволит поддерживать порядок на сетевом диске и своевременно удалять ненужные файлы, а также покажет ошибки с путями в лекциях. **Работает для 2.0 и более поздних версий.**

Импортируем все необходимые библиотеки:

In [ ]:
from bs4 import BeautifulSoup
import requests
import base64
import json

Для начала работы введите номер проверяемой ветви и свой GitHub Access Token в ячейку ниже и выполните её:

In [ ]:
github_token = "Input Your GitHub Access Token Here"
dev_brunch = "dev-2.0"

Сперва необходимо авторизироваться на GitHub:

In [ ]:
headers = {}
if github_token:
    headers['Authorization'] = f"token {github_token}"

Сначала стучимся в гитхаб и получаем оттуда названия лекций.

*В настоящее время такой способ не подойдет, так как названия парсятся из дефолтной ветки, и в ней названия не совпадают с dev-2.0, поэтому пока этот код закомментирован.*

In [ ]:
# url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/?ref={dev_brunch}'
# r = requests.get(url, headers=headers)
# r.raise_for_status()
# data = r.json()
# lectures = [x['name'] for x in data[2:17]]

В связи с этим зададим названия лекций вручную:

In [ ]:
lectures = ['L01_Intro.ipynb', 'L02_Linear_models.ipynb', 'L03_Classic_ML.ipynb', 'L04_Feature_Engineering.ipynb', 'L05_Neural_networks.ipynb', 'L06_CNN.ipynb', 'L07_Learning_techniques.ipynb', 'L08_NN_architectures.ipynb', 'L09_RNN.ipynb', 'L10_Transformers.ipynb', 'L11_Segmentation_Detection.ipynb', 'L12_Representation_learning.ipynb', 'L13_Generative_models.ipynb', 'L14_Explainability.ipynb', 'L15_RL.ipynb']

## Проверка лишних файлов на сетевом диске

Теперь напишем функцию, которая будет делать полный процесс сравнения папок **EduNet-content** и **EduNet-web_dependencies** для одной лекции. Выполните ячейку:

In [ ]:
def compare_notebook_files_and_host(lecture): #lecture in lectures:

    print(lecture)

    lecture_num = lecture.split("_")[0] # Получаем короткий номер лекции из имени типа "L01" для вставки в пути

    # Загружаем содержимое блокнота
    url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_brunch}'
    r = requests.get(url, headers=headers)
    r.raise_for_status()
    data = r.json()
    file_content = data['content']
    file_content_encoding = data.get('encoding')
    if file_content_encoding == 'base64':
        file_content = base64.b64decode(file_content).decode()
    file_content = json.loads(file_content)

    links = []

    for k in range(len(file_content["cells"])):
        cell_text = ','.join(file_content["cells"][k]['source'])
        temp_cell = cell_text.replace("http", " http")  # Добавим искусственно пробелы, чтобы по ним разделить, если в ячейке есть две картинки без пробелов
        one_cell = temp_cell.split(" ")
        for i in range(0, len(one_cell)):
            if("http" in one_cell[i] and "edunet.kea.su" in one_cell[i]):
                link = one_cell[i][one_cell[i].find("http") :]
                #print(link)
                # А теперь попробуем убрать немного лишнего справа и свести в общий список по всем ячейкам
                if("\n" in link):
                    link = link[ : link.find("\n")]
                if('"' in link):
                    link = link[ : link.find('"')]
                if("'" in link):
                    link = link[ : link.find("'")]
                links.append(link)

    print("Всего файлов: ", len(links))
    # for i in range (0, len(links)):
    #    print(links[i], "\n")

    # Теперь мы получили список всех ссылок, и пришло время разделить из на content и web_dependencies
    content_in_lection = []
    wd_in_lection = []
    mistakes_in_lection = []
    datasets_in_lection = []
    weights_in_lection = []


    content_in_host = []
    wd_in_host = []
    mistakes_in_host = []
    datasets_in_host = []
    weights_in_host = []

    # Составляем все списки по блокнотам
    for i in range(0, len(links)):
        if("//edunet.kea.su/repo/EduNet-web_dependencies/"+dev_brunch+"/"+lecture_num in links[i]):
            wd_in_lection.append(links[i].split("/")[-1])
        elif("//edunet.kea.su/repo/EduNet-content/"+dev_brunch+"/"+lecture_num in links[i]):
            content_in_lection.append(links[i].split("/")[-1])
        elif("//edunet.kea.su/repo/EduNet-web_dependencies/datasets/" in links[i]):
            datasets_in_lection.append(links[i])
        elif("//edunet.kea.su/repo/EduNet-web_dependencies/weights/" in links[i]):
            weights_in_lection.append(links[i])
        else:
            mistakes_in_lection.append(links[i])

    # Парсим сетевой
    #get url like
    url = f'https://edunet.kea.su/repo/EduNet-content/{dev_brunch}/{lecture_num}/out/'
    html_text = requests.get(url).text

    image_links = BeautifulSoup(html_text, 'lxml').find_all(href=True)[1:]

    for link in image_links:
        content_in_host.append(("".join([url, link.get('href')])).split("/")[-1])

    url = f'https://edunet.kea.su/repo/EduNet-web_dependencies/{dev_brunch}/{lecture_num}/'
    html_text = requests.get(url).text

    image_links = BeautifulSoup(html_text, 'lxml').find_all(href=True)[1:]

    for link in image_links:
        wd_in_host.append(("".join([url, link.get('href')])).split("/")[-1])

    # print("Web Dependencies:\n", set(wd_in_host) - set(wd_in_lection))
    # print("Content: \n", set(content_in_host) - set(content_in_lection))

    if(set(wd_in_host) == set(wd_in_lection)):
        print("In folder EduNet-web_dependencies all right!")
    else:
        wd_set = set(wd_in_host) - set(wd_in_lection)
        wd_list = list(wd_set)
        print("Web Dependencies:")
        for i in range(0, len(wd_list)):
            print(wd_list[i])
        print("\n")

    if(set(content_in_host) == set(content_in_lection)):
        print("In folder EduNet-content all right!")
    else:
        content_set = set(content_in_host) - set(content_in_lection)
        content_list = list(content_set)
        print("Content:")
        for i in range(0, len(content_list)):
            print(content_list[i])
        print("\n")

print('Done!')

Присвойте переменной `lection_num` номер проверяемой лекции от $1$ до $15$, и Вы получите полный список **лишних** файлов на сетевом диске, которых **уже нет в блокнотах**. Ячейку можно выполнять много раз для любых лекций.

In [ ]:
lection_num = 4
# dev_brunch = "dev-2.0"  # Тут можно переопределить ветку для удобства
compare_notebook_files_and_host(lectures[lection_num-1])

## Проверка недостающих файлов на сетевом диске

Эта функция проверяет наличие в блокнотах битых ссылок (если на сетевом диске было удалено что-то лишнее):

In [ ]:
def check_lection(lecture): #lecture in lecture_names:

    print(lecture)

    lecture_num = lecture.split("_")[0] # Получаем короткий номер лекции из имени типа "L01" для вставки в пути

    url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_brunch}'
    r = requests.get(url, headers=headers)
    r.raise_for_status()
    data = r.json()
    file_content = data['content']
    file_content_encoding = data.get('encoding')
    if file_content_encoding == 'base64':
        file_content = base64.b64decode(file_content).decode()
    file_content = json.loads(file_content)

    links = []
    for k in range(len(file_content["cells"])):
        cell_text = ','.join(file_content["cells"][k]['source'])
        temp_cell = cell_text.replace("http", " http")  # Добавим искусственно пробелы, чтобы по ним разделить, если в ячейке есть две картинки без пробелов, потому что вариант получше я пока не нашла
        one_cell = temp_cell.split(" ")
        for i in range(0, len(one_cell)):
            if("http" in one_cell[i] and "edunet.kea.su" in one_cell[i]):
                link = one_cell[i][one_cell[i].find("http") :]
                #print(link)
                # А теперь попробуем убрать немного лишнего справа и свести в общий список по всем ячейкам
                if("\n" in link):
                    link = link[ : link.find("\n")]
                if('"' in link):
                    link = link[ : link.find('"')]
                if("'" in link):
                    link = link[ : link.find("'")]
                links.append(link)


    # print(len(links))
    # for i in range (0, len(links)):
    #     print(links[i], "\n")

    # Теперь мы получили список всех ссылок, и пришло время разделить их на content и web_dependencies
    content_in_lection = []
    wd_in_lection = []
    mistakes_in_lection = []
    datasets_in_lection = []
    weights_in_lection = []


    content_in_host = []
    wd_in_host = []
    mistakes_in_host = []
    datasets_in_host = []
    weights_in_host = []

    # Составляем все списки по блокнотам
    for i in range(0, len(links)):
        if("//edunet.kea.su/repo/EduNet-web_dependencies/"+dev_brunch+"/"+lecture_num in links[i]):
            wd_in_lection.append(links[i].split("/")[-1])
        elif("//edunet.kea.su/repo/EduNet-content/"+dev_brunch+"/"+lecture_num in links[i]):
            content_in_lection.append(links[i].split("/")[-1])
        elif("//edunet.kea.su/repo/EduNet-web_dependencies/datasets/" in links[i]):
            datasets_in_lection.append(links[i])
        elif("//edunet.kea.su/repo/EduNet-web_dependencies/weights/" in links[i]):
            weights_in_lection.append(links[i])
        else:
            mistakes_in_lection.append(links[i])

    # Парсим сетевой

    #get url like
    url = f'https://edunet.kea.su/repo/EduNet-content/{dev_brunch}/{lecture_num}/out/'
    html_text = requests.get(url).text

    image_links = BeautifulSoup(html_text, 'lxml').find_all(href=True)[1:]

    for link in image_links:
        content_in_host.append(("".join([url, link.get('href')])).split("/")[-1])

    url = f'https://edunet.kea.su/repo/EduNet-web_dependencies/{dev_brunch}/{lecture_num}/'
    html_text = requests.get(url).text

    image_links = BeautifulSoup(html_text, 'lxml').find_all(href=True)[1:]

    for link in image_links:
        wd_in_host.append(("".join([url, link.get('href')])).split("/")[-1])

    # print("Web Dependencies:\n", set(wd_in_host) - set(wd_in_lection))
    # print("Content: \n", set(content_in_host) - set(content_in_lection))

    wd_set = set(wd_in_lection) - set(wd_in_host)
    content_set = set(content_in_lection) - set(content_in_host)
    wd_list = list(wd_set)
    content_list = list(content_set)

    print("Web Dependencies:")
    for i in range(0, len(wd_list)):
        print(wd_list[i])
    print("\n")
    print("Content:")
    for i in range(0, len(content_list)):
        print(content_list[i])

print('Done!')

И аналогично введем номер лекции и получим аналитику:

In [ ]:
num = 15
# dev_brunch = "dev-2.0"  # Тут можно переопределить ветку для удобства
check_lection(lectures[num-1])

## Дополнительно: веса, датасеты, странные ссылки

Здесь можно получить информацию по всем дополнительным файлам (сторонним весам и датасетам), а также по ошибкам в ссылках по всем лекциям сразу. Не сравнивается с сетевым диском. При необходимости можно будет добавить этот функционал.

In [ ]:
for lecture in lectures:

    print(lecture)

    lecture_num = lecture.split("_")[0] # Получаем короткий номер лекции из имени типа "L01" для вставки в пути

    url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_brunch}'
    r = requests.get(url, headers=headers)
    r.raise_for_status()
    data = r.json()
    file_content = data['content']
    file_content_encoding = data.get('encoding')
    if file_content_encoding == 'base64':
        file_content = base64.b64decode(file_content).decode()
    file_content = json.loads(file_content)

    links = []
    for k in range(len(file_content["cells"])):
        cell_text = ','.join(file_content["cells"][k]['source'])
        temp_cell = cell_text.replace("http", " http")  # Добавим искусственно пробелы, чтобы по ним разделить, если в ячейке есть две картинки без пробелов, потому что вариант получше я пока не нашла
        one_cell = temp_cell.split(" ")
        for i in range(0, len(one_cell)):
            if("http" in one_cell[i] and "edunet.kea.su" in one_cell[i]):
                link = one_cell[i][one_cell[i].find("http") :]
                #print(link)
                # А теперь попробуем убрать немного лишнего справа и свести в общий список по всем ячейкам
                if("\n" in link):
                    link = link[ : link.find("\n")]
                if('"' in link):
                    link = link[ : link.find('"')]
                links.append(link)

    # Теперь мы получили список всех ссылок, и пришло время разделить их на content и web_dependencies
    content_in_lection = []
    wd_in_lection = []
    mistakes = []
    datasets = []
    weights = []

    # Составляем все списки по блокнотам
    for i in range(0, len(links)):
        if("//edunet.kea.su/repo/EduNet-web_dependencies/"+dev_brunch+"/"+lecture_num in links[i]):
            wd_in_lection.append(links[i].split("/")[-1])
        elif("//edunet.kea.su/repo/EduNet-content/"+dev_brunch+"/"+lecture_num in links[i]):
            content_in_lection.append(links[i].split("/")[-1])
        elif("//edunet.kea.su/repo/EduNet-web_dependencies/datasets/" in links[i]):
            datasets.append(links[i])
        elif("//edunet.kea.su/repo/EduNet-web_dependencies/weights/" in links[i]):
            weights.append(links[i])
        else:
            mistakes.append(links[i])

    # Если что-то не нужно, можно закомментировать

    # 1. Печатать весов из всех лекций
    # if(len(weights)>0):
    #     print("Weights:")
    #     for i in range(0, len(weights)):
    #         print(weights[i])

    # 2. Печатать датасетов из всех лекций
    if(len(datasets)>0):
        print("Datasets:")
        datasets_unique  = []
        for i in range(0, len(datasets)):
            if datasets[i] not in datasets_unique:
                datasets_unique.append(datasets[i])
        for i in range (0, len(datasets_unique)):
            print((datasets_unique[i]))

    # 3. Печать ошибочных ссылок
    # if(len(mistakes)>0):
    #     print("Mistakes:")
    #     for i in range(0, len(mistakes)):
    #         print(mistakes[i])